# Exercice 3 - Review questions

**a) Assuming an univariate input *x*, what is the complexity at inference time of a Bayesian classifier based on histogram computation of the likelihood ?**

For each class, we must compute the likelyhood, which is one calculus per class, so O(nb_class). Then, for each x we must compute the posteriori probability, which is looking into a pre-computed histogram (done in the training phase), so this is O(nb_class). The a priori probability only needs to be computed for each class, so O(nb_class). So, the total complexity of the Bayesian classifier is O(2 * nb_class * nb_x)

**b) Bayesian models are said to be generative as they can be used to generate new samples. Taking the implementation of the exercise 1.a, explain the steps to generate new samples using the system you have put into place.**
 

To generate a new sample, we need to create a y and a x. This can be done by firstly picking the class Ck randomly according to the a priori probabilities P(Ck). This means that, if there is two classes and P(C1) = 0.6 and P(C2) = 0.4, we take 60% of the time C1 and 40% of the time C2

Then, we can pick a random x based on the probability density function p(x|Ck). This means we choose a class and, in the density function (like histogram), we take a random x based on the probablilities. If there is two x values possibles and one is distributed as 0.4 and the other 0.6, we will taxe x1 40% of the time and x2 60%

***Optional*: Provide an implementation in a function generateSample(priors, histValues, edgeValues, n)**

In [ ]:
def generateSample(priors, histValues, edgeValues, n):
    # pick a class according to the proba
    # to do that, compute the different probabilities sum. This is done by creating intervals between 0 and 1. The size of those intervals represents the probability of the random
    # number generator to land on it.
    cumulative_probs = np.cumsum(priors)

    # take a random number and see in which interval it falls. The index of this interval will be the class we chose
    chosen_class = 0
    r = random.random() 
    for i, cp in enumerate(cumulative_probs):
        if r < cp:
            chosen_class = i
            break
    

    # The same logic is used to find the new x value. We take the proba of x given c and chose randomly weighted by those proba.
    # we have to compute the "probabilities" differently, because the histogram is only the count of each x in the c.
    # here, we kept the count instead of proba and when generating the random number, instead of chosing between 0 1 and 1 we chose between 0 and total_hist
    # which does the same job in the end
    total_hist = np.sum(histValues[chosen_class])

    cumulative_probs_hist = np.cumsum(histValues[chosen_class])

    # take a random number and see in which interval it falls. The index of this interval will be the class we chose
    chosen_x_index = 0
    r = random.uniform(0, total_hist) 
    for i, cp in enumerate(cumulative_probs_hist):
        if r < cp:
            chosen_x_index = i
            break

    chosen_x = edgeValues[chosen_x_index]
    


**c) What is the minimum overall accuracy of a 2-class system relying only on priors and that is built on a training set that includes 5 times more samples in class A than in class B?**

If we only take the priors, then A has 5/6 chances to be chosen vs B 1/6. The minimum accuracy is then 5/6, because the system will choose based on the 5/6 and 1/6, which will yeild 5/6 good results

**d) Let’s look back at the PW02 exercise 3 of last week. We have built a knn classification systems for images of digits on the MNIST database.**

**How would you build a Bayesian classification for the same task ? Comment on the prior probabilities and on the likelihood estimators. More specifically, what kind of likelihood estimator could we use in this case ?**

The a priori probability is simply the repartition of each class in the dataset.
The likelihood is the tricky part, because the system would need to be multivariate (because of all the pixels), which makes it very complex. We could use the Naive Bayes formula witch states that the features (pixels) are completely uncorrelated and then we cound perform the operation pixel per pixel for each image. However, the pixels ARE NOT uncorrelated, because a pixel is spatially positionned. If a pixel is white, there is a strong change that there are white pixels somewhere around as well. The Naive Bayes would technically still work-ish, but with a false presomption.

To do it correctly, we would have to use something like the multivariate gaussian distribution

***Optional:* implement it and report performance !**

In [2]:
pass

**e) Read [europe-border-control-ai-lie-detector](https://theintercept.com/2019/07/26/europe-border-control-ai-lie-detector/). The described system is "a virtual policeman designed to strengthen European borders". It can be seen as a 2-class problem, either you are a suspicious traveler or you are not. If you are declared as suspicious by the system, you are routed to a human border agent who analyses your case in a more careful way.**

1. What kind of errors can the system make ? Explain them in your own words.
2. Is one error more critical than the other ? Explain why.
3. According to the previous points, which metric would you recommend to tune your MLsystem ?

1. The system can make false positives or false negatives. This means it could say that an innocent man is a threat or that a dangerous person is safe to cross the border.
2. Yes, a false negative is the most critical one. In the case of a false positive, the only consequence is a lost of time because you have to interrogate the "suspect", maybe resulting in a angry customer. On the other hand, a false negative means a real threat has entered the country and has not been detect, wich could have way more concequences than an angry customer.
3. In this case, we could use the Area Under the Curve with this system. This would allow to tune the the treshold and impact the decision to tend more to false positives rather than false negatives

**f) When a deep learning architecture is trained using an unbalanced training set, we usually observe a problem of bias, i.e. the system favors one class over another one. Using the Bayes equation, explain what is the origin of the problem.**

The bayes equation : P(Ck|x) = (p(x|Ck)*P(Ck))/p(x).

The a priori probability (P(Ck)) is what reprensents the unbalance in the training set. This value is the probability to have this class, so it is linked to the number of data in it. This means that a class with 3x more data in it will have a way bigger P(Ck) witch will impact the decision in favor of the biggest P(Ck).